In [10]:
import psycopg2

# 数据库连接参数
db_params = {
    'dbname': 'harbintrips',  # 连接到默认的 postgres 数据库
    'user': 'username',   # 替换为你的用户名
    'password': 'password', # 替换为你的密码
    'host': 'localhost',
    'port': '5432'
}

# 创建连接
try:
    conn = psycopg2.connect(**db_params)
    cur = conn.cursor()

    # 创建表 SQL 语句
    create_table_query = """
    CREATE TABLE IF NOT EXISTS trip_se4(
        id SERIAL PRIMARY KEY,               -- 自动递增的主键
        devid INTEGER NOT NULL,
        trip_id INTEGER NOT NULL,
        st_lon DOUBLE PRECISION NOT NULL, -- 起始经度（地理坐标）
        st_lat DOUBLE PRECISION NOT NULL,  -- 起始纬度（地理坐标）
        st_timestamp BIGINT,          -- 起始时间（时间戳）
        ed_lon DOUBLE PRECISION NOT NULL, -- 到达经度（地理坐标）
        ed_lat DOUBLE PRECISION NOT NULL,  -- 到达纬度（地理坐标）
        ed_timestamp BIGINT          -- 到达时间（时间戳）
    );
    """

    # 执行创建表的 SQL
    cur.execute(create_table_query)
    conn.commit()

    print("表 'trip_se4' 创建成功！")

except Exception as e:
    print("发生错误：", e)

finally:
    # 关闭连接
    if cur:
        cur.close()
    if conn:
        conn.close()

表 'trip_se4' 创建成功！


In [11]:
import h5py

# 打开 HDF5 文件
file_path = "/home/dk/Code/Python/zhongtai/data/trips_150104.h5"
# trip_se2
# 打开 HDF5 文件

with h5py.File(file_path, 'r') as h5_file:
    # 查看顶层结构
    print("顶层结构:")
    print(list(h5_file.keys()))

    # 查看 'trip' 下的数据结构
    print("\n'trip' 下的子组:")
    try:
        conn = psycopg2.connect(**db_params)
        # 存入pgsql
        insert_query = """
        INSERT INTO trip_se4 (devid, trip_id, st_lon, st_lat, st_timestamp, ed_lon, ed_lat, ed_timestamp)
        VALUES (%s, %s, %s, %s, %s, %s, %s, %s);
        """
        # 遍历每个 trip 的数据
        for trip_id in h5_file['trip']:
            trip_group = h5_file[f'trip/{trip_id}']
            tmslist = trip_group['tms'][:].tolist()
            st_timestamp = min(tmslist)
            ed_timestamp = max(tmslist)
            st_index = tmslist.index(st_timestamp)
            ed_index = tmslist.index(ed_timestamp)
            st_lon = trip_group['lon'][st_index]
            st_lat = trip_group['lat'][st_index]
            ed_lon = trip_group['lon'][ed_index]
            ed_lat = trip_group['lat'][ed_index]
            
            data = {
                "trip_id": int(trip_id),
                "devid": int(trip_group['devid'][()]),
                "st_lon": float(st_lon),
                "st_lat": float(st_lat),
                "st_timestamp": int(st_timestamp),
                "ed_lon": float(ed_lon),
                "ed_lat": float(ed_lat),
                "ed_timestamp": int(ed_timestamp),
            }
            record = (data['devid'], 
                    data['trip_id'], 
                    data['st_lon'], 
                    data['st_lat'], 
                    data['st_timestamp'], 
                    data['ed_lon'], 
                    data['ed_lat'], 
                    data['ed_timestamp'])
            cur = conn.cursor()
            # 执行创建表的 SQL
            cur.execute(insert_query, record)
            print("已存入trip:", trip_id)
            conn.commit()
    except Exception as e:
        print("发生错误：", e)

    finally:
        # 关闭连接
        if cur:
            cur.close()
        if conn:
            conn.close()


顶层结构:
['meta', 'trip']

'trip' 下的子组:
已存入trip: 1
已存入trip: 10
已存入trip: 100
已存入trip: 1000
已存入trip: 10000
已存入trip: 100000
已存入trip: 100001
已存入trip: 100002
已存入trip: 100003
已存入trip: 100004
已存入trip: 100005
已存入trip: 100006
已存入trip: 100007
已存入trip: 100008
已存入trip: 100009
已存入trip: 10001
已存入trip: 100010
已存入trip: 100011
已存入trip: 100012
已存入trip: 100013
已存入trip: 100014
已存入trip: 100015
已存入trip: 100016
已存入trip: 100017
已存入trip: 100018
已存入trip: 100019
已存入trip: 10002
已存入trip: 100020
已存入trip: 100021
已存入trip: 100022
已存入trip: 100023
已存入trip: 100024
已存入trip: 100025
已存入trip: 100026
已存入trip: 100027
已存入trip: 100028
已存入trip: 100029
已存入trip: 10003
已存入trip: 100030
已存入trip: 100031
已存入trip: 100032
已存入trip: 100033
已存入trip: 100034
已存入trip: 100035
已存入trip: 100036
已存入trip: 100037
已存入trip: 100038
已存入trip: 100039
已存入trip: 10004
已存入trip: 100040
已存入trip: 100041
已存入trip: 100042
已存入trip: 100043
已存入trip: 100044
已存入trip: 100045
已存入trip: 100046
已存入trip: 100047
已存入trip: 100048
已存入trip: 100049
已存入trip: 10005
已存入trip: 100050
已存入trip